In [1]:
from fbprophet import Prophet
import pandas as pd
import numpy as np
from fbprophet.plot import plot_plotly, plot_components_plotly
import plotly.graph_objects as go

In [125]:
def get_covid_data():
    
    #get the latest data from OxCGRT
    DATA_URL = 'https://raw.githubusercontent.com/OxCGRT/covid-policy-tracker/master/data/OxCGRT_latest.csv'
    full_df = pd.read_csv(DATA_URL,
                    parse_dates=['Date'],
                    encoding="ISO-8859-1",
                    dtype={"RegionName": str,
                           "RegionCode":str,
                           "CountryName":str,
                           "CountryCode":str},
                    error_bad_lines=False)

    #add new cases and new deaths columns

    return full_df

def mean_percent_error(y_test, y_hat):
    from math import e
    error = np.abs(y_test - y_hat)
    percent_error = error/(y_test + e)
    mean_percent_error = percent_error.sum() / len(y_test)
    return mean_percent_error

def find_best_regressors(df, train_df, test_df):
    todrop = [c for c in df.columns if c in ['ds','y','NewCases','NewDeaths', 'ConfirmedCases','ConfirmedDeaths']]
    regressors = df.columns.drop(todrop)

    keepers = []
    trials = pd.DataFrame(columns = ['regressors','MAPE'])
    improving = True
    while improving:
        best = None
        improving = False

        print(f'current keepers are {keepers}')
        for regressor in regressors:
            keepers.append(regressor)
            m = pr.Prophet(seasonality_mode = 'multiplicative',
                            yearly_seasonality = False, 
                            daily_seasonality = False, 
                            weekly_seasonality = True)
            m.add_country_holidays(country_name='US')
            for keeper in keepers:
                m.add_regressor(keeper)
            m.fit(train_df)
            future = m.make_future_dataframe(periods=len(test_df))
            future = pd.merge(future,df[['ds'] + keepers].reset_index(drop=True),how = 'outer', on = 'ds')
            forecast = m.predict(future)
            prophet_mape = mean_percent_error(test_df['y'].values, forecast['yhat'][-len(test_df):].values)
            trials = trials.append({'regressors':f'{keepers}','MAPE':prophet_mape}, ignore_index=True)
            #MAPE has improved
            if prophet_mape == trials['MAPE'].min():
                improving = True
                best = regressor
            keepers.pop()
        if best:
            keepers.append(best)
        if improving:
            regressors = regressors.drop(best)
    return keepers

def train_prophet(train_df, test_df, additional_regressors=None, growth='linear'):
    m = Prophet(seasonality_mode = 'multiplicative',
                yearly_seasonality = False, 
                daily_seasonality = False, 
                weekly_seasonality = True,
               growth=growth)
    m.add_country_holidays(country_name='US')
    if additional_regressors is not None:
        for regressor in additional_regressors:
            m.add_regressor(regressor)
    m.fit(train_df)
    future = m.make_future_dataframe(periods=len(test_df))
    if additional_regressors is not None:
        future = pd.merge(future, additional_regressors, how = 'inner', 
                          left_on = 'ds', right_index=True)
    forecast = m.predict(future)
    return m, forecast

# Acquire latest data and prepare dataframe
The variables at the top of the cell can be adjusted to get data on different regions.  Because some entries are at the country level and some are at the regional level, you can specify which level you want in the `division` variable.

In [134]:
#'country' or 'state'
division = 'country'
region = 'United States'
#'ConfirmedCases' or 'ConfirmedDeaths'
prediction = 'ConfirmedCases'

full_df = get_covid_data()
if division == 'country':
    df = full_df[(full_df['Jurisdiction'] == 'NAT_TOTAL') & (full_df['CountryName'] == region)][:-1]
elif division == 'state':
    df = full_df[(full_df['Jurisdiction'] == 'STATE_TOTAL') & (full_df['RegionName'] == region)][:-1]

#remove unneeded columns
df = df.iloc[:,5:]
cols = [c for c in df.columns if (c.lower()[-10:] != 'fordisplay') and (c.lower()[-4:] != 'flag')]
df = df[cols]

#drop columns with not data and fill missing data with either previous data or 0
df = df.dropna(how='all', axis=1)
df = df.fillna(method = 'ffill')
df = df.fillna(0)

#rename date and target variables to work with fbprophet
df = df.rename(columns = {'Date':'ds',
                          prediction:'y'
                          })
df = df.drop(columns = [col for col in df.columns if col in ['ConfirmedDeaths','ConfirmedCases']])

#train-test split
train_df = df[df['ds'] < '2020-12-01']
test_df = df[df['ds'] >= '2020-12-01']

additional_regressors = df[test_df.columns.drop(['y'])].set_index('ds', drop=True)

## Prediction using only case rates

In [135]:
m, forecast = train_prophet(train_df, test_df)
prophet_mape = mean_percent_error(test_df['y'].values, forecast['yhat'][-len(test_df):].values)
print(f'MAPE without exogenous variables is {prophet_mape}')

fig = plot_plotly(m, forecast, changepoints = False, xlabel="Date", 
                  uncertainty = True,
                  ylabel=prediction, plot_cap=True)
fig.add_trace(go.Scatter(x=test_df['ds'], y=test_df['y'], 
                         mode = 'markers',
                         marker=go.scatter.Marker(color='green', size = 4),
                         name = f'True'
                         ))
fig.show()

MAPE without exogenous variables is 0.1850509065394809


fbprophet model is off by an average of 20ish percent with no additional variables outside of target variable trends.

## Comparing Non-Pharmaceutical Intervention (NPI) Intensity Strategies :
The below graph compares what happens to the model's predictions for December when government interventions are frozen at 2020-12-01 values, when they have the actual value that they did, and if they are raised by 10 points.

In [136]:
#Actual government responses

m, forecast = train_prophet(train_df, test_df, additional_regressors)
prophet_mape = mean_percent_error(test_df['y'].values, forecast['yhat'][-len(test_df):].values)
print(f'MAPE using actual government interventions is {prophet_mape}')

#Freeze Government Interventions at 2020-12-01
frozen_regressors_12_1 = additional_regressors.copy()
for col in frozen_regressors_12_1:
    frozen_regressors_12_1.loc[frozen_regressors_12_1.index >= '2020-12-01',col] \
                    = df.loc[df['ds'] == '2020-12-01',col].values[0]

m_frozen, frozen_forecast = train_prophet(train_df, test_df, frozen_regressors_12_1)
prophet_mape_frozen = mean_percent_error(test_df['y'].values, frozen_forecast['yhat'][-len(test_df):].values)
print(f'Mean actual percent error if interventions are not changed from 12-01-2020 is {prophet_mape_frozen}')

#Increase Government Response Indices by 10
increased_regressors = additional_regressors.copy()
increased_regressors.loc[increased_regressors.index >= '2020-12-01','GovernmentResponseIndex'] \
                = df.loc[df['ds'] == '2020-12-01','GovernmentResponseIndex'].values[0] +10
increased_regressors.loc[increased_regressors.index >= '2020-12-01','ContainmentHealthIndex'] \
                = df.loc[df['ds'] == '2020-12-01','ContainmentHealthIndex'].values[0] +10

m_increased, forecast_increased = train_prophet(train_df, test_df, increased_regressors)
prophet_mape_increased = mean_percent_error(test_df['y'].values, forecast_increased['yhat'][-len(test_df):].values)
print(f'Mean actual percent error if interventions are increased is {prophet_mape_increased}')

fig = plot_plotly(m, forecast, changepoints = False, xlabel="Date", 
                  uncertainty = True,
                  ylabel=prediction, plot_cap=True)
fig.add_trace(go.Scatter(x=test_df['ds'], y=test_df['y'], 
                         mode = 'markers',
                         marker=go.scatter.Marker(color='green', size = 4),
                         name = f'True'
                         ))
fig.add_trace(go.Scatter(x=frozen_forecast['ds'], y =frozen_forecast['yhat'],
                         marker=go.scatter.Marker(color='yellow', size = 4),
                         name = f'prediction if frozen'
                         ))
fig.add_trace(go.Scatter(x=forecast_increased['ds'], y=forecast_increased['yhat'], 
                         mode = 'lines',
                         marker=go.scatter.Marker(color='red', size = 4),
                         name = f'prediction if increased'
                         ))
fig.layout.title = {'text': f'True and Predicted {prediction} in {region}'}
fig.update_layout(showlegend=True)
fig.show()

MAPE using actual government interventions is 0.2374335672956442
Mean actual percent error if interventions are not changed from 12-01-2020 is 0.15778392103275463
Mean actual percent error if interventions are increased is 0.22900441121861165


## Conclusions


# Lagging NPIs
I'll try a range of lags, from 5 days, the average onset time of COVID according to [Harvard Health](https://www.health.harvard.edu/diseases-and-conditions/covid-19-basics#:~:text=Recently%20published%20research%20found%20that,long%20as%2013%20days%20later), to 25 days, enough time for transmissions to propagate.

In [ ]:
lag_errors = pd.DataFrame(columns = ['errors'])
for lag in range(0,26):
    lagged_regressors = additional_regressors.shift(periods=lag,freq='d',fill_value=0)
    lagged_regressors = pd.merge(df['ds'], lagged_regressors, 
                                 how='left', left_on='ds', right_index=True)
    lagged_regressors = lagged_regressors.set_index('ds', drop=True).fillna(0)
    m, forecast = train_prophet(train_df, test_df, lagged_regressors)
    mape = mean_percent_error(df['y'].values[-len(test_df):], 
                              forecast['yhat'].values[-len(test_df):])
    lag_errors.loc[lag] = [mape]
    fig = plot_plotly(m, forecast)
    fig.layout.title = {'text':f'Lag {lag}'}
    fig.update_layout(showlegend = True)
    fig.add_trace(go.Scatter(x=test_df['ds'], y=test_df['y'], 
                             mode = 'markers',
                             marker=go.scatter.Marker(color='green', size = 4),
                             name = f'True Test'
                             ))
    fig.show()
                        
lag_errors.plot()

In [138]:
lag_errors

errors
5   0.223446
6   0.220714
7   0.218007
8   0.215324
9   0.212666
10  0.210032
11  0.207420
12  0.204824
13  0.202245
14  0.199683
15  0.197144
16  0.197086
17  0.197029
18  0.196963
19  0.196886
20  0.196737
21  0.196586
22  0.196437
23  0.197819
24  0.199169
25  0.200500

That didn't seem to help much.